In [14]:
#Importing necessary libraries

import yfinance as yf
import pandas as pd
import numpy as np
import requests
from datetime import datetime
import time



In [15]:
#Get S&P 500 tickers function

def get_sp500_tickers():
    """
    Fetch S&P 500 tickers. Fix Yahoo format: '.' -> '-'.
    Fallback to DataHub if Wikipedia is blocked.
    """
    try:
        print("🔍 fetching S&P 500 from Wikipedia…")
        headers = {"User-Agent": "Mozilla/5.0"}
        url = "https://en.wikipedia.org/wiki/List_of_S%26P_500_companies"
        html = requests.get(url, headers=headers, timeout=20).text
        tables = pd.read_html(html)
        tickers = tables[0]["Symbol"].tolist()
    except Exception as e:
        print(f"⚠️ wikipedia failed ({e}); using DataHub fallback…")
        url = "https://datahub.io/core/s-and-p-500-companies/r/constituents.csv"
        tickers = pd.read_csv(url)["Symbol"].tolist()

    tickers = [t.replace(".", "-").strip().upper() for t in tickers]
    print(f"✅ got {len(tickers)} tickers")
    return tickers

sp500 = get_sp500_tickers()


🔍 fetching S&P 500 from Wikipedia…
✅ got 503 tickers


/var/folders/6n/p578p__s54j_ngsncpgm562m0000gn/T/ipykernel_79859/3324319269.py:13: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  tables = pd.read_html(html)


In [16]:
# Adding extra tickers and options
extra_tickers = ["BRK-B", "ARKK"]   # add anything you want here
include_index = True
include_gold = True
include_rf    = True

tickers = sp500.copy()
if include_index: tickers.append("^GSPC")
if include_gold:  tickers.append("GC=F")
if include_rf:    tickers.append("^IRX")
tickers += extra_tickers

print("📊 total to fetch:", len(tickers))


📊 total to fetch: 508


In [17]:
#Download historical data
start = "2020-01-01"
end   = datetime.today().strftime("%Y-%m-%d")
print(f"⏳ downloading {start} → {end}")

t0 = time.time()
data = yf.download(
    tickers,
    start=start,
    end=end,
    progress=True,
    group_by="ticker",   # MultiIndex: ('Ticker','Price')
    threads=False,       # more reliable on many networks
    auto_adjust=False,   # consistent OHLCV
    timeout=30
)
print(f"⏱️ bulk download took {(time.time()-t0):.1f}s")

if data.empty:
    raise RuntimeError("Download returned empty DataFrame.")



⏳ downloading 2020-01-01 → 2025-11-04


[*********************100%***********************]  507 of 507 completed

⏱️ bulk download took 144.4s


In [18]:
print("Type:", type(data))
print("Index:", type(data.index))
print("Col level names:", getattr(data.columns, "names", None))
print("Sample columns:", data.columns[:10])
display(data)


Type: <class 'pandas.core.frame.DataFrame'>
Index: <class 'pandas.core.indexes.datetimes.DatetimeIndex'>
Col level names: ['Ticker', 'Price']
Sample columns: MultiIndex([('MDLZ',      'Open'),
            ('MDLZ',      'High'),
            ('MDLZ',       'Low'),
            ('MDLZ',     'Close'),
            ('MDLZ', 'Adj Close'),
            ('MDLZ',    'Volume'),
            ( 'PSX',      'Open'),
            ( 'PSX',      'High'),
            ( 'PSX',       'Low'),
            ( 'PSX',     'Close')],
           names=['Ticker', 'Price'])


Ticker           MDLZ                                                          \
Price            Open       High        Low      Close  Adj Close      Volume   
Date                                                                            
2020-01-02  55.060001  55.349998  54.110001  54.330002  47.267025   7272900.0   
2020-01-03  54.000000  54.570000  53.959999  54.240002  47.188732   6791700.0   
2020-01-06  54.389999  54.480000  53.849998  54.150002  47.110447   5906400.0   
2020-01-07  54.049999  54.080002  53.570000  53.919998  46.910328   6716300.0   
2020-01-08  54.029999  54.419998  53.910000  54.049999  47.023418   5435400.0   
...               ...        ...        ...        ...        ...         ...   
2025-10-28  61.599998  62.430000  60.209999  60.209999  60.209999  15035000.0   
2025-10-29  58.470001  59.270000  56.990002  57.849998  57.849998  20841600.0   
2025-10-30  58.240002  59.259998  57.630001  57.779999  57.779999  12884300.0   
2025-10-31  56.970001  57.939999  56.630001  57.459999  57.459999  13262800.0   
2025-11-03  57.439999  57.840000  56.540001  56.650002  56.650002   8848800.0   

Ticker             PSX                                      ...         ABT  \
Price             Open        High         Low       Close  ...         Low   
Date                                                        ...               
2020-01-02  112.080002  113.180000  111.379997  112.199997  ...   85.800003   
2020-01-03  111.250000  112.419998  108.190002  108.489998  ...   85.589996   
2020-01-06  108.239998  108.440002  107.209999  107.809998  ...   85.209999   
2020-01-07  107.129997  108.220001  106.739998  108.139999  ...   85.540001   
2020-01-08  108.320000  108.440002  103.809998  104.099998  ...   85.930000   
...                ...         ...         ...         ...  ...         ...   
2025-10-28  134.070007  135.740005  133.660004  133.660004  ...  126.190002   
2025-10-29  132.539993  138.779999  130.800003  138.000000  ...  124.120003   
2025-10-30  137.270004  141.369995  136.059998  137.070007  ...  124.330002   
2025-10-31  136.699997  137.649994  135.250000  136.139999  ...  122.610001   
2025-11-03  136.720001  138.929993  134.580002  137.919998  ...  122.440002   

Ticker                                              GEHC             \
Price            Close   Adj Close     Volume       Open       High   
Date                                                                  
2020-01-02   86.949997   78.208046  4969000.0        NaN        NaN   
2020-01-03   85.889999   77.254616  4747000.0        NaN        NaN   
2020-01-06   86.339996   77.659393  5631700.0        NaN        NaN   
2020-01-07   85.860001   77.227623  3408100.0        NaN        NaN   
2020-01-08   86.209999   77.542412  5693900.0        NaN        NaN   
...                ...         ...        ...        ...        ...   
2025-10-28  126.610001  126.610001  4763000.0  78.120003  79.750000   
2025-10-29  124.430000  124.430000  5182000.0  76.739998  78.385002   
2025-10-30  124.669998  124.669998  4877400.0  77.379997  77.379997   
2025-10-31  123.620003  123.620003  7044900.0  74.639999  75.190002   
2025-11-03  123.839996  123.839996  5833000.0  74.830002  75.870003   

Ticker                                                  
Price             Low      Close  Adj Close     Volume  
Date                                                    
2020-01-02        NaN        NaN        NaN        NaN  
2020-01-03        NaN        NaN        NaN        NaN  
2020-01-06        NaN        NaN        NaN        NaN  
2020-01-07        NaN        NaN        NaN        NaN  
2020-01-08        NaN        NaN        NaN        NaN  
...               ...        ...        ...        ...  
2025-10-28  77.680000  79.400002  79.400002  5877000.0  
2025-10-29  73.730003  77.379997  77.379997  8765300.0  
2025-10-30  73.949997  75.000000  75.000000  3474800.0  
2025-10-31  73.519997  74.949997  74.949997  3275700.0  
2025-11-03  73.638000 

In [19]:
# Saving row DataFrame to CSV
data.to_csv("sp500_data.csv")

In [ ]:
data.columns = [f"{ticker}_{field}".replace(" ", "").replace("/", "") 
                for ticker, field in data.columns]

#sort columns alphabeticall
data = data.reindex(sorted(data.columns), axis=1)

# Save cleaned data
data.to_csv("market_data.csv")

print("✅ Cleaned and saved as 'market_data.csv'")


ValueError: too many values to unpack (expected 2)

AAPL_AdjClose  AAPL_Close   AAPL_High    AAPL_Low   AAPL_Open  \
Date                                                                        
2020-01-02      72.538506   75.087502   75.150002   73.797501   74.059998   
2020-01-03      71.833282   74.357498   75.144997   74.125000   74.287498   
2020-01-06      72.405678   74.949997   74.989998   73.187500   73.447502   
2020-01-07      72.065163   74.597504   75.224998   74.370003   74.959999   
2020-01-08      73.224411   75.797501   76.110001   74.290001   74.290001   
...                   ...         ...         ...         ...         ...   
2025-10-28     269.000000  269.000000  269.890015  268.149994  268.989990   
2025-10-29     269.700012  269.700012  271.410004  267.109985  269.279999   
2025-10-30     271.399994  271.399994  274.140015  268.480011  271.989990   
2025-10-31     270.369995  270.369995  277.320007  269.160004  276.989990   
2025-11-03     269.049988  269.049988  270.850006  266.250000  270.420013   

            AAPL_Volume  ABBV_AdjClose  ABBV_Close   ABBV_High    ABBV_Low  \
Date                                                                         
2020-01-02  135480400.0      69.823448   89.550003   89.570000   88.510002   
2020-01-03  146322800.0      69.160706   88.699997   89.389999   87.900002   
2020-01-06  118387200.0      69.706490   89.400002   89.620003   87.980003   
2020-01-07  108872000.0      69.308853   88.889999   89.540001   88.260002   
2020-01-08  132079200.0      69.800041   89.519997   90.059998   88.870003   
...                 ...            ...         ...         ...         ...   
2025-10-28   41534800.0     227.539993  227.539993  228.399994  224.309998   
2025-10-29   51086700.0     225.139999  225.139999  228.000000  224.039993   
2025-10-30   69886500.0     228.199997  228.199997  229.649994  226.410004   
2025-10-31   86167100.0     218.039993  218.039993  223.869995  216.000000   
2025-11-03   50138700.0     211.960007  211.960007  219.000000  211.690002   

            ...   ^GSPC_High    ^GSPC_Low   ^GSPC_Open  ^GSPC_Volume  \
Date        ...                                                        
2020-01-02  ...  3258.139893  3235.530029  3244.669922  3.459930e+09   
2020-01-03  ...  3246.149902  3222.340088  3226.360107  3.484700e+09   
2020-01-06  ...  3246.840088  3214.639893  3217.550049  3.702460e+09   
2020-01-07  ...  3244.909912  3232.429932  3241.860107  3.435910e+09   
2020-01-08  ...  3267.070068  3236.669922  3238.590088  3.726840e+09   
...         ...          ...          ...          ...           ...   
2025-10-28  ...  6911.299805  6870.729980  6897.740234  5.695930e+09   
2025-10-29  ...  6920.339844  6851.910156  6910.950195  6.280130e+09   
2025-10-30  ...  6880.750000  6820.689941  6860.500000  6.052700e+09   
2025-10-31  ...  6879.169922  6814.259766  6879.169922  6.398280e+09   
2025-11-03  ...  6882.319824  6820.620117  6882.319824  6.065720e+09   

            ^IRX_AdjClose  ^IRX_Close  ^IRX_High  ^IRX_Low  ^IRX_Open  \
Date                                                                    
2020-01-02          1.495       1.495      1.510     1.495      1.510   
2020-01-03          1.473       1.473      1.490     1.460      1.490   
2020-01-06          1.488       1.488      1.490     1.475      1.478   
2020-01-07          1.500       1.500      1.505     1.500      1.505   
2020-01-08          1.493       1.493      1.493     1.485      1.493   
...                   ...         ...        ...       ...        ...   
2025-10-28          3.720       3.720      3.730     3.720      3.725   
2025-10-29          3.730       3.730      3.730     3.700      3.713   
2025-10-30          3.757       3.757      3.788     3.755      3.760   
2025-10-31          3.718       3.718      3.743     3.715      3.740   
2025-11-03          3.783       3.783      3.788     3.728      3.728   

            ^IRX_Volume  
Date                     
2020-01-02          0.0  
2020-01-03          0.0  
2020